<a href="https://colab.research.google.com/github/Linda0628/hhh/blob/main/plotplot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##Reading the dataset

In [ ]:
##Importing the libraries
!pip install py-openaq
!pip install folium
!pip install shapely
!pip install geopandas

import seaborn as sns
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import warnings

In [ ]:
# Importing data on Cities

import openaq

api = openaq.OpenAQ()

status, resp = api.cities()

In [ ]:
#Picking the data from the Open AQ API
resp = api.latest(df=True, limit=10000)

In [ ]:
#Reading the first two rows of the data
resp.head(2)

parameter  ...  averagingPeriod.unit
lastUpdated                          ...                      
2021-12-04 06:15:00+00:00       no2  ...               seconds
2021-12-04 06:15:00+00:00      pm10  ...               seconds

[2 rows x 9 columns]

In [ ]:
#Finding more about the number of columns and rows
print('The dataset has ', resp.shape[1], 'columns and ', resp.shape[0], 'rows.')

The dataset has  9 columns and  35580 rows.


In [ ]:
#Finding out about the datatypes of our dataset
resp.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 35580 entries, 2021-12-04 06:15:00+00:00 to 2019-12-27 08:00:00+00:00
Data columns (total 9 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   parameter              35580 non-null  object 
 1   value                  35580 non-null  float64
 2   unit                   35580 non-null  object 
 3   sourceName             35580 non-null  object 
 4   country                35580 non-null  object 
 5   city                   35580 non-null  object 
 6   location               35580 non-null  object 
 7   averagingPeriod.value  34094 non-null  float64
 8   averagingPeriod.unit   35580 non-null  object 
dtypes: float64(2), object(7)
memory usage: 2.7+ MB


In [ ]:
#Making the index a column
resp.reset_index(level=0, inplace=True)

In [ ]:
#Checking out the columns in our dataset
resp.columns

Index(['lastUpdated', 'parameter', 'value', 'unit', 'sourceName', 'country',
       'city', 'location', 'averagingPeriod.value', 'averagingPeriod.unit'],
      dtype='object')

In [ ]:
#Splitting the date and time into two separate columns
resp['time'],resp['date']= resp['lastUpdated'].apply(lambda x:x.time()), resp['lastUpdated'].apply(lambda x:x.date())
resp.head(2)

lastUpdated parameter  ...      time        date
0 2021-12-04 06:15:00+00:00       no2  ...  06:15:00  2021-12-04
1 2021-12-04 06:15:00+00:00      pm10  ...  06:15:00  2021-12-04

[2 rows x 12 columns]

##Creating the geographical map.

In [ ]:
!pip install plotly
!pip install cufflinks


In [ ]:
import plotly.graph_objs as go 
from plotly.offline import init_notebook_mode,iplot,plot
init_notebook_mode(connected=True)

import pandas as pd

In [ ]:
data = dict(
        type = 'choropleth',
        colorscale = 'Viridis',
        locations = resp['city'],
        locationmode = "country names",
        z = resp['value'],
        text = resp['city'],
        colorbar = {'title' : 'Power Consumption KWH'},
      )


In [ ]:
layout = dict(title = '2014 Power Consumption KWH',
              geo = dict(projection = {'type':'mercator'})
             )

In [ ]:
choromap = go.Figure(data = [data],layout = layout)
iplot(choromap,validate=False)

In [ ]:
fig = px.choropleth(resp, locations="parameter",
                    color="value",
                    hover_name="city",
                    animation_frame="date",
                    title = "Covid Cases plotted using Plotly",                 color_continuous_scale=px.colors.sequential.PuRd)
 
 
fig["layout"].pop("updatemenus")
fig.show()

ValueError: ignored

In [ ]:
import plotly.express as px

fig = px.choropleth(resp, geojson=country, locations='parameter', color='value',
                           color_continuous_scale="Viridis",
                           range_color=(0, 12),
                           labels={'parameter':'parameter'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

NameError: ignored

In [ ]:
import pandas as pd
import plotly as py
from plotly.offline import download_plotlyjs,init_notebook_mode,plot,iplot

In [ ]:
init_notebook_mode(connected=True)

In [ ]:
#Installing the necessary library
!pip install opencage

In [ ]:
from opencage.geocoder import OpenCageGeocode

In [ ]:
key = '0fdd2e2ef2a647158a9836b860f87f68'  # get api key from:  https://opencagedata.com

geocoder = OpenCageGeocode(key)

In [ ]:
#Creating a for loop to map the geo locations
list_lat = []   # create empty lists

list_long = []


	
for index, row in resp.iterrows(): # iterate over rows in dataframe



    City = row['city']       
    query = str(City)

    results = geocoder.geocode(query)   
    lat = results[0]['geometry']['lat']
    long = results[0]['geometry']['lng']

    list_lat.append(lat)
    list_long.append(long)

	
# create new columns from lists    

resp['lat'] = list_lat   

resp['lon'] = list_long

IndexError: ignored